# Recipe Scraping Analysis 

In [69]:
from pymongo import MongoClient
import pandas as pd 
pd.set_option('display.max_columns', None) 
from IPython.display import display 
from ingredient_parser import parse_ingredient
import regex as re 
import spacy

In [2]:
# Connect to MongoDB
client = MongoClient()
db = client['recipe_db']  # Replace with your database name

# List all collections (tables)
collections = db.list_collection_names()
print("Collections:", collections)

Collections: ['whatsgabycooking', 'sallysbakingaddiction', 'wellplated', 'acouplecooks_recipes', 'wedishitup', 'ahealthysliceoflife', 'abeautifulmess_recipes']


In [3]:
# Function to convert all collections into a single DataFrame
def load_all_collections(db):
    all_data = []  # List to store all documents

    for collection_name in db.list_collection_names():
        collection = db[collection_name]  # Access collection
        documents = list(collection.find())  # Convert to list
        for doc in documents:
            doc['_collection'] = collection_name  # Track source collection
            doc.pop('_id', None)  # Remove MongoDB's default `_id`
        all_data.extend(documents)

    # Convert list of dicts to DataFrame
    df = pd.DataFrame(all_data)
    return df

# Load into DataFrame
df = load_all_collections(db)

In [4]:
df.head()

canonical_url                  host  \
0    https://whatsgabycooking.com/meal-plan-week-20/  whatsgabycooking.com   
1  https://whatsgabycooking.com/14-of-our-favorit...  whatsgabycooking.com   
2   https://whatsgabycooking.com/raspberry-brownies/  whatsgabycooking.com   
3  https://whatsgabycooking.com/pineapple-sheet-c...  whatsgabycooking.com   
4   https://whatsgabycooking.com/magic-bar-brownies/  whatsgabycooking.com   

                                               image language  \
0  https://whatsgabycooking.com/wp-content/upload...    en-US   
1  https://whatsgabycooking.com/wp-content/upload...    en-US   
2  https://whatsgabycooking.com/wp-content/upload...    en-US   
3  https://whatsgabycooking.com/wp-content/upload...    en-US   
4  https://whatsgabycooking.com/wp-content/upload...    en-US   

             site_name       _collection       author       category  \
0  What's Gaby Cooking  whatsgabycooking          NaN            NaN   
1  What's Gaby Cooking  whatsgabycooking  Gaby Dalkin        Dessert   
2  What's Gaby Cooking  whatsgabycooking  Gaby Dalkin        Dessert   
3  What's Gaby Cooking  whatsgabycooking  Gaby Dalkin        Dessert   
4  What's Gaby Cooking  whatsgabycooking  Gaby Dalkin  Dessert,Snack   

   cook_time   cuisine                                        description  \
0        NaN       NaN                                                NaN   
1       20.0  American  Strawberry Blueberry Shortcakes are the desser...   
2       50.0  American  These Raspberry Swirled Brownies are the most ...   
3       35.0  American  Pineapple Sheet Cake – the breakfast and desse...   
4       60.0  American  Magic Bar Brownies have been big since before ...   

                                   ingredient_groups  \
0                                                NaN   
1  [{'ingredients': ['3 cups all purpose flour', ...   
2  [{'ingredients': ['240 grams dark chocolate (a...   
3  [{'ingredients': ['2 cups white sugar', '2 egg...   
4  [{'ingredients': ['240 grams dark chocolate (a...   

                                         ingredients  \
0                                                NaN   
1  [3 cups all purpose flour, 2 teaspoons lemon z...   
2  [240 grams dark chocolate (approximately 1½ cu...   
3  [2 cups white sugar, 2 eggs (at room temperatu...   
4  [240 grams dark chocolate (approx 1½ cups regu...   

                                        instructions  \
0                                                NaN   
1  For the Biscuits\nCombine the flour, lemon zes...   
2  Preheat the oven to 325° F.\nCombine the choco...   
3  Preheat the oven to 350 degrees F.\nLine a 9x1...   
4  Preheat the oven to 325° F. Line a 9×13 pan wi...   

                                   instructions_list  \
0                                                NaN   
1  [For the Biscuits, Combine the flour, lemon ze...   
2  [Preheat the oven to 325° F., Combine the choc...   
3  [Preheat the oven to 350 degrees F., Line a 9x...   
4  [Preheat the oven to 325° F. Line a 9×13 pan w...   

                                            keywords  \
0                                                NaN   
1        [strawberry shortcake, blueberry shortcake]   
2  [brownies, raspberry brownies, how to make bro...   
3      [cream cheese frosting, pineapple sheet cake]   
4                                    [best brownies]   

                                           nutrients  prep_time  ratings  \
0                                                NaN        NaN      NaN   
1  {'calories': '731 kcal', 'carbohydrateContent'...       15.0     5.00   
2  {'calories': '358 kcal', 'carbohydrateContent'...       10.0     4.67   
3  {'calories': '233 kcal', 'carbohydrateContent'...       15.0     4.81   
4  {'calories': '611 kcal', 'carbohydrateContent'...       30.0     5.00   

   ratings_count                                            title  total_time  \
0            NaN                                            

In [5]:
# data cleaning

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9848 entries, 0 to 9847
Data columns (total 26 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   canonical_url         9848 non-null   object 
 1   host                  9848 non-null   object 
 2   image                 9823 non-null   object 
 3   language              9848 non-null   object 
 4   site_name             9848 non-null   object 
 5   _collection           9848 non-null   object 
 6   author                8916 non-null   object 
 7   category              8470 non-null   object 
 8   cook_time             6030 non-null   float64
 9   cuisine               8346 non-null   object 
 10  description           8915 non-null   object 
 11  ingredient_groups     8923 non-null   object 
 12  ingredients           8930 non-null   object 
 13  instructions          9000 non-null   object 
 14  instructions_list     9000 non-null   object 
 15  keywords             

In [7]:
df = df[
    ~((df['ingredients'].isna()) | df['ingredients'].astype(str).isin(['{}', '[]'])) & 
    ~((df['instructions'].isna()) | df['instructions'].astype(str).isin(['{}', '[]']))
]

In [8]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 8819 entries, 1 to 9847
Data columns (total 26 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   canonical_url         8819 non-null   object 
 1   host                  8819 non-null   object 
 2   image                 8819 non-null   object 
 3   language              8819 non-null   object 
 4   site_name             8819 non-null   object 
 5   _collection           8819 non-null   object 
 6   author                8819 non-null   object 
 7   category              8445 non-null   object 
 8   cook_time             5965 non-null   float64
 9   cuisine               8329 non-null   object 
 10  description           8818 non-null   object 
 11  ingredient_groups     8812 non-null   object 
 12  ingredients           8819 non-null   object 
 13  instructions          8819 non-null   object 
 14  instructions_list     8819 non-null   object 
 15  keywords             

In [9]:
nutrition_df = df[df['nutrients']!= {}] # 5k recipes not bad 
nutrition_df['category'].value_counts()

Main Course                    686
Dessert                        676
Side Dish                      433
Breakfast                      353
Main Dish                      323
                              ... 
Breakfast,Drinks,Smoothie        1
Snacks                           1
Appetizer,Snack,Lunch            1
Main Course,Lunch,Breakfast      1
brunch,Drinks                    1
Name: category, Length: 241, dtype: int64

In [10]:
nutrition_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 5582 entries, 1 to 9847
Data columns (total 26 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   canonical_url         5582 non-null   object 
 1   host                  5582 non-null   object 
 2   image                 5582 non-null   object 
 3   language              5582 non-null   object 
 4   site_name             5582 non-null   object 
 5   _collection           5582 non-null   object 
 6   author                5582 non-null   object 
 7   category              5544 non-null   object 
 8   cook_time             4153 non-null   float64
 9   cuisine               5481 non-null   object 
 10  description           5582 non-null   object 
 11  ingredient_groups     5578 non-null   object 
 12  ingredients           5582 non-null   object 
 13  instructions          5582 non-null   object 
 14  instructions_list     5582 non-null   object 
 15  keywords             

In [11]:
print(nutrition_df['ingredient_groups'].loc[1])

[{'ingredients': ['3 cups all purpose flour', '2 teaspoons lemon zest', '3 tablespoons granulated sugar', '1 1/2 tablespoons baking powder', '1 teaspoon salt', '12 tablespoons cold unsalted butter (cut into small pieces)', '1 1/2 cups heavy cream', '1 1/2 teaspoons vanilla extract'], 'purpose': 'For the Shortcakes'}, {'ingredients': ['1 pound strawberries (tops removed and sliced)', '1/3 cup white sugar', '1 pint blueberries'], 'purpose': 'For the Strawberries + Blueberries'}, {'ingredients': ['2 cups heavy cream', '2/3 cup powdered sugar', '2 teaspoons vanilla extract'], 'purpose': 'For the Cream'}]


In [12]:
nutrition_df['ingredients'].loc[1]

['3 cups all purpose flour',
 '2 teaspoons lemon zest',
 '3 tablespoons granulated sugar',
 '1 1/2 tablespoons baking powder',
 '1 teaspoon salt',
 '12 tablespoons cold unsalted butter (cut into small pieces)',
 '1 1/2 cups heavy cream',
 '1 1/2 teaspoons vanilla extract',
 '1 pound strawberries (tops removed and sliced)',
 '1/3 cup white sugar',
 '1 pint blueberries',
 '2 cups heavy cream',
 '2/3 cup powdered sugar',
 '2 teaspoons vanilla extract']

In [183]:
indr = nutrition_df[['canonical_url', 'ingredients', 'nutrients', 'dietary_restrictions']]
indr.head()

canonical_url  \
1  https://whatsgabycooking.com/14-of-our-favorit...   
2   https://whatsgabycooking.com/raspberry-brownies/   
3  https://whatsgabycooking.com/pineapple-sheet-c...   
4   https://whatsgabycooking.com/magic-bar-brownies/   
5  https://whatsgabycooking.com/grilled-peaches-w...   

                                         ingredients  \
1  [3 cups all purpose flour, 2 teaspoons lemon z...   
2  [240 grams dark chocolate (approximately 1½ cu...   
3  [2 cups white sugar, 2 eggs (at room temperatu...   
4  [240 grams dark chocolate (approx 1½ cups regu...   
5  [2 ripe peaches, 2 ripe nectarines, canola oil...   

                                           nutrients dietary_restrictions  
1  {'calories': '731 kcal', 'carbohydrateContent'...                  NaN  
2  {'calories': '358 kcal', 'carbohydrateContent'...                  NaN  
3  {'calories': '233 kcal', 'carbohydrateContent'...                  NaN  
4  {'calories': '611 kcal', 'carbohydrateContent'...                  NaN  
5  {'calories': '166 kcal', 'carbohydrateContent'...                  NaN

In [93]:
# establish all ingredient names 

def extract_text_with_spaces(string):
    """Extract only letters, commas, and spaces from a given string."""
    return ' '.join(re.findall(r'[A-Za-z,]+', string))

def find_entity_indices(text, entity):
    start = text.lower().find(entity.lower())  # Case-insensitive search
    if start == -1:
        print(f"⚠️ Entity '{entity}' not found in text: '{text}'")  # Debugging output
        return None  # Return None if entity is not found
    end = start + len(entity)
    return {"entities":[(start, end, "INGREDIENT")]}

In [114]:
ingredient_lists = indr['ingredients'].to_list()
ingredients_list = []
for i in ingredient_lists:
    # ingredients_stripped = extract_text_with_spaces(str(i)).split(',')
    ingredients_list+=i #ngredients_stripped
    
all_ingredients = list(set(ingredients_list))
print(all_ingredients[:10], len(all_ingredients))

['', '3/4 cup whole wheat flour (or additional all purpose flour)', '2-4 tablespoons red onion (thinly sliced)', '1 pound fresh green beans or haricots verts (ends trimmed and patted VERY dry)', 'Freshly Cracked black pepper', '1 1/4 cups chopped pecans', 'Cilantro, finely chopped\xa0', '1 beef boullion cube', '1 cup semi sweet chocolate chips, plus one handful, divided', 'Sour cream (as needed)'] 29008


In [115]:
print(all_ingredients)
all_ingredients = all_ingredients[1:]

['', '3/4 cup whole wheat flour (or additional all purpose flour)', '2-4 tablespoons red onion (thinly sliced)', '1 pound fresh green beans or haricots verts (ends trimmed and patted VERY dry)', 'Freshly Cracked black pepper', '1 1/4 cups chopped pecans', 'Cilantro, finely chopped\xa0', '1 beef boullion cube', '1 cup semi sweet chocolate chips, plus one handful, divided', 'Sour cream (as needed)', '4 ½ oz chocolate (dark)', '4 to 6 radishes', '1/2 teaspoon nutmeg (divided (freshly grated if possible)', '6 ounces okra (fresh )', '6 eggs (or any number that fits in the pot without touching)', '2 teaspoons chopped fresh za’atar or oregano', 'potato chips (to serve)', '4 pounds 1 1/2-inch-diameter baby potatoes (scrubbed, cut into small pieces)', '1 tablespoon peanut butter (or almond butter )', '1/4 head Red cabbage (thinly sliced)', '1 cup freshly shredded reduced-fat sharp cheddar cheese (plus additional for serving)', '1/2 cup fresh basil, torn', '1 bunch dinosaur kale, finely shredded

In [117]:
unique_ingredient_columns = []
ingredient_columns = set() # for final product
fixed_ings = []
for ing in all_ingredients:
    info = parse_ingredient(ing)
    if info.name != []:
        for sub_ing in info.name:
            print(sub_ing)
            info_name = sub_ing.text.lower()
            if info_name not in unique_ingredient_columns and info_name not in fixed_ings:
                print
                if sub_ing.confidence < .90:
                    pass
                    # print(f"ingredient in recipe: {ing}\nproposed ingredient: {info_name}")
                    # response = input("if changing ingredient type new name, else enter")
                    # if response == '':
                    #     unique_ingredient_columns.add(info_name)
                    # elif response[0] == '/':
                    #     continue
                    # else:
                    #     unique_ingredient_columns.add(response[1:])
                else:
                    # print(info)
                    # Example
                    text = ing
                    entity = info_name
                    ingredient_columns.add(entity)
                    result = find_entity_indices(text.lower(), entity)  # Output: (14, 23)
                    if result != None:
                        unique_ingredient_columns.append((text.lower(), result))

IngredientText(text='whole wheat flour', confidence=0.99549, starting_index=2)
IngredientText(text='red onion', confidence=0.996367, starting_index=2)
IngredientText(text='fresh green beans', confidence=0.816608, starting_index=2)
IngredientText(text='haricots verts', confidence=0.994796, starting_index=6)
IngredientText(text='black pepper', confidence=0.996449, starting_index=2)
IngredientText(text='pecans', confidence=0.995445, starting_index=3)
IngredientText(text='Cilantro', confidence=0.996561, starting_index=0)
IngredientText(text='beef boullion cube', confidence=0.955421, starting_index=1)
IngredientText(text='semi sweet chocolate chips', confidence=0.996164, starting_index=2)
IngredientText(text='Sour cream', confidence=0.998851, starting_index=0)
IngredientText(text='chocolate (dark)', confidence=0.94664, starting_index=2)
IngredientText(text='radishes', confidence=0.998108, starting_index=1)
IngredientText(text='nutmeg', confidence=0.998126, starting_index=2)
IngredientText(t

In [107]:
print(len(unique_ingredient_columns)) #7536/27230 ~30% of ingredients 
train_data = unique_ingredient_columns
train_data[:20]

27449


[('3/4 cup whole wheat flour (or additional all purpose flour)',
  {'entities': [(8, 25, 'INGREDIENT')]}),
 ('2-4 tablespoons red onion (thinly sliced)',
  {'entities': [(16, 25, 'INGREDIENT')]}),
 ('1 pound fresh green beans or haricots verts (ends trimmed and patted very dry)',
  {'entities': [(29, 43, 'INGREDIENT')]}),
 ('freshly cracked black pepper', {'entities': [(16, 28, 'INGREDIENT')]}),
 ('1 1/4 cups chopped pecans', {'entities': [(19, 25, 'INGREDIENT')]}),
 ('cilantro, finely chopped\xa0', {'entities': [(0, 8, 'INGREDIENT')]}),
 ('1 beef boullion cube', {'entities': [(2, 20, 'INGREDIENT')]}),
 ('1 cup semi sweet chocolate chips, plus one handful, divided',
  {'entities': [(6, 32, 'INGREDIENT')]}),
 ('sour cream (as needed)', {'entities': [(0, 10, 'INGREDIENT')]}),
 ('4 ½ oz chocolate (dark)', {'entities': [(7, 23, 'INGREDIENT')]}),
 ('4 to 6 radishes', {'entities': [(7, 15, 'INGREDIENT')]}),
 ('1/2 teaspoon nutmeg (divided (freshly grated if possible)',
  {'entities': [(13, 1

In [109]:
from spacy.training.example import Example 
nlp = spacy.load("en_core_web_sm")

# Add labels to the NER pipeline
ner = nlp.get_pipe("ner")
for _, annotations in train_data:
    for ent in annotations.get("entities"):
        ner.add_label(ent[2])

# Disable other pipelines during training
unaffected_pipes = [pipe for pipe in nlp.pipe_names if pipe != "ner"]

# Train the NER model
with nlp.disable_pipes(*unaffected_pipes):
    optimizer = nlp.resume_training()
    for i in range(20):  # Training for 20 iterations
        print(f"Iteration {i+1}")
        for text, annotations in train_data:
            example = Example.from_dict(nlp.make_doc(text), annotations)
            nlp.update([example], drop=0.3, sgd=optimizer)

# Save the trained model
nlp.to_disk("ingredient_ner_model")
print("Model training complete and saved to 'ingredient_ner_model'.")

Iteration 1


/Users/bryce/anaconda3/lib/python3.11/site-packages/spacy/training/iob_utils.py:149: UserWarning: [W030] Some entities could not be aligned in the text "2 tablespoons dutch process /dark cocoa powder (or..." with entities "[(14, 29, 'INGREDIENT')]". Use `spacy.training.offsets_to_biluo_tags(nlp.make_doc(text), entities)` to check the alignment. Misaligned entities ('-') will be ignored during training.
  warnings.warn(
/Users/bryce/anaconda3/lib/python3.11/site-packages/spacy/training/iob_utils.py:149: UserWarning: [W030] Some entities could not be aligned in the text "2 tablespoons dutch process /dark cocoa powder (or..." with entities "[(29, 46, 'INGREDIENT')]". Use `spacy.training.offsets_to_biluo_tags(nlp.make_doc(text), entities)` to check the alignment. Misaligned entities ('-') will be ignored during training.
  warnings.warn(


Iteration 2
Iteration 3
Iteration 4
Iteration 5
Iteration 6
Iteration 7
Iteration 8
Iteration 9
Iteration 10
Iteration 11
Iteration 12
Iteration 13
Iteration 14
Iteration 15
Iteration 16
Iteration 17
Iteration 18
Iteration 19
Iteration 20
Model training complete and saved to 'ingredient_ner_model'.


In [119]:
for ing in all_ingredients:
    info = parse_ingredient(ing)
    if info.name != []:
        for sub_ing in info.name:
            info_name = sub_ing.text.lower()
            if info_name not in unique_ingredient_columns and info_name not in fixed_ings:
                if sub_ing.confidence < .90:
                    doc = nlp(info_name)
                    # print(f"Input: {info_name}")
                    # print("Entities:", [(ent.text, ent.label_) for ent in doc.ents])
                    for ent in doc.ents:
                        ingredient_columns.add(ent.text)

In [124]:
print(len(ingredient_columns), ingredient_columns)

6479 {'mini dark chocolate chips', 'gruyere cheese', 'simply nature organic classic hummus', 'full fat sour cream', 'steaming hot water', 'croissants', 'parsely', 'heirloom plum tomatoes', 'fresh chives from the aerogarden', 'canned mexicorn', 'raw pepitas', 'aged rum', 'black cod fillets', 'chili paste', 'high quality hummus*', 'flank iron steak', 'seedless cucumber', 'crème fraîche', 'russet potato*', 'pumpkin pie spice, maple pecan granola', 'short whole wheat pasta of choice', 'rotel tomatoes', 'roasted red bell peppers', 'sun dried tomatoes packed in oil (julienne-cut)', 'red onions', 'francis mangos', 'white frosting of choice', 'canned borlotti beans', 'leftover', 'no salt added tomato paste', 'long brown rice', 'white', 'sweet variation', 'other dark leafy greens', 'canned corn', 'other sparkling wine', 'roast beef', 'pork belly', "gaby's everyday", 'charred jalapeno', 'pure lemon extract', 'prosciutto', 'fire-roasted tomatoes in their juices', 'coconut flour***', 'corn on the 

In [126]:
def clean_text(text):
    """Removes all characters except spaces, hyphens, and a-z letters (case-insensitive)."""
    return re.sub(r"[^a-zA-Z\s\-]", "", text)

In [159]:
ingredient_columns_list = list(ingredient_columns)
for item in range(len(ingredient_columns_list)):
    cleaned_text = clean_text(ingredient_columns_list[item])
    ingredient_columns_list[item] = cleaned_text
ingredient_columns_list=list(set(ingredient_columns_list))
ingredient_columns_list.pop(1)

''

In [172]:
print(len(ingredient_columns_list))
poss_ing_update = set()

for ing in ingredient_columns_list:
    info = parse_ingredient(ing)
    if info.name != []:
        for sub_ing in info.name:
            info_name = sub_ing.text.lower()
            if info_name not in unique_ingredient_columns and info_name not in fixed_ings:
                if sub_ing.confidence > .90:
                    poss_ing_update.add(info_name)

print(len(poss_ing_update))

6008
5432


In [165]:
#recipe pipeline 
ingredient_df_base = nutrition_df[['canonical_url', 'ingredients']]

def clean_recipe_ings(recipe_ing_list, ing_columns, nlp):
    """
    Cleans ingredient names and creates a binary presence list.
    
    Args:
        recipe_ing_list (list): List of ingredients for a single recipe.
        ing_columns (set): Set of all unique ingredient names.
        nlp (spacy.Language): Trained spaCy model for ingredient parsing.
    
    Returns:
        dict: Dictionary with ingredients as keys and binary values (1 if present, 0 if not).
    """
    this_recipe_ingredients = set()  # Use a set to avoid duplicates

    for ing in recipe_ing_list:
        info = parse_ingredient(ing)  # Use ingredient parser
        if info.name:
            for sub_ing in info.name:
                info_name = sub_ing.text.lower()
                if sub_ing.confidence > 0.90:
                    this_recipe_ingredients.add(info_name)
                else:
                    doc = nlp(info_name)  # Use NER to extract ingredients
                    for ent in doc.ents:
                        this_recipe_ingredients.add(ent.text.lower())

    # Clean ingredient names (removing numbers, special characters, etc.)
    this_recipe_ingredients = [clean_text(ing) for ing in this_recipe_ingredients]
    # Convert to binary dictionary (1 = present, 0 = absent)
    ingredient_presence = {ing: 1 if ing in this_recipe_ingredients else 0 for ing in ing_columns}
    # print(sum(ingredient_presence.values()))

    return ingredient_presence

In [263]:
# Extract all unique ingredients from the dataset
ingredient_columns_list = list(ingredient_columns)
for item in range(len(ingredient_columns_list)):
    cleaned_text = clean_text(ingredient_columns_list[item])
    ingredient_columns_list[item] = cleaned_text
ingredient_columns_list=list(set(ingredient_columns_list))
ingredient_columns_list.pop(1)
poss_ing_update = set()

for ing in ingredient_columns_list:
    info = parse_ingredient(ing)
    if info.name != []:
        for sub_ing in info.name:
            info_name = sub_ing.text.lower()
            if info_name not in unique_ingredient_columns and info_name not in fixed_ings:
                if sub_ing.confidence > .90:
                    poss_ing_update.add(info_name)
# Create a DataFrame where each row is a recipe, and columns are ingredients
recipe_ingredient_matrix = []

for recipe in ingredient_df_base["ingredients"]:  # Loop through each recipe
    ingredient_presence = clean_recipe_ings(recipe, list(poss_ing_update), nlp)
    recipe_ingredient_matrix.append(ingredient_presence)

# Convert list of dictionaries to DataFrame
ingredient_df = pd.DataFrame(recipe_ingredient_matrix)

# Add Recipe IDs if available
ingredient_df.insert(0, "recipe_id", ingredient_df_base["canonical_url"])  # Add recipe IDs for reference
ingredient_df.head()

recipe_id  \
0                                                NaN   
1  https://whatsgabycooking.com/14-of-our-favorit...   
2   https://whatsgabycooking.com/raspberry-brownies/   
3  https://whatsgabycooking.com/pineapple-sheet-c...   
4   https://whatsgabycooking.com/magic-bar-brownies/   

   mini dark chocolate chips  gruyere cheese  japanese cucumbers  \
0                          0               0                   0   
1                          0               0                   0   
2                          0               0                   0   
3                          0               0                   0   
4                          0               0                   0   

   simply nature organic classic hummus  full fat sour cream  croissants  \
0                                     0                    0           0   
1                                     0                    0           0   
2                                     0                    0           0   
3                                     0                    0           0   
4                                     0                    0           0   

   heirloom plum tomatoes  fresh chives from the aerogarden  \
0                       0                                 0   
1                       0                                 0   
2                       0                                 0   
3                       0                                 0   
4                       0                                 0   

   -cheese tortellini  canned mexicorn  raw pepitas  aged rum  \
0                   0                0            0         0   
1                   0                0            0         0   
2                   0                0            0         0   
3                   0                0            0         0   
4                   0                0            0         0   

   black cod fillets  chili paste  paneer  flank iron steak  \
0                  0            0       0                 0   
1                  0            0       0                 0   
2                  0            0       0                 0   
3                  0            0       0                 0   
4                  0            0       0                 0   

   seedless cucumber  short whole wheat pasta of choice  rotel tomatoes  \
0                  0                                  0               0   
1                  0                                  0               0   
2                  0                                  0               0   
3                  0                                  0               0   
4                  0                                  0               0   

   roasted red bell peppers  red onions  francis mangos  \
0                         0           0               0   
1                         0           0               0   
2                         0           0               0   
3                         0           0               0   
4                         0           0               0   

   white frosting of choice  canned borlotti beans  leftover  long brown rice  \
0                         0                      0         0                0   
1                         0                      0         0                0   
2                         0                      0         0                0   
3                         0                      0         0                0   
4                         0                      0         0                0   

   white  sweet variation  other dark leafy greens  \
0      0                0                        0   
1      0                0                        0   
2      0                0                        0   
3      0                0                        0   
4      0                0                        0   

   andes crme de menthe baking chips  canned corn  other sparkling wine  

In [264]:
ingredient_df_c = ingredient_df 

In [185]:
# break out recipes by nutritional info 
macros_df = pd.json_normalize(indr['nutrients'])
macros_df.insert(0, "recipe_id", ingredient_df_base["canonical_url"])
macros_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5582 entries, 0 to 5581
Data columns (total 13 columns):
 #   Column                 Non-Null Count  Dtype 
---  ------                 --------------  ----- 
 0   recipe_id              3565 non-null   object
 1   calories               5578 non-null   object
 2   carbohydrateContent    5548 non-null   object
 3   proteinContent         5522 non-null   object
 4   fatContent             5516 non-null   object
 5   saturatedFatContent    5426 non-null   object
 6   transFatContent        3770 non-null   object
 7   cholesterolContent     4753 non-null   object
 8   sodiumContent          4190 non-null   object
 9   fiberContent           5382 non-null   object
 10  sugarContent           5492 non-null   object
 11  unsaturatedFatContent  2963 non-null   object
 12  servingSize            3963 non-null   object
dtypes: object(13)
memory usage: 567.1+ KB


In [187]:
macros_func = macros_df[~((macros_df['calories'].isna()) | (macros_df['carbohydrateContent'].isna()) | (macros_df['proteinContent'].isna()) | (macros_df['fatContent'].isna()))]
macros_func.head()

recipe_id  calories  \
0                                                NaN  731 kcal   
1  https://whatsgabycooking.com/14-of-our-favorit...  358 kcal   
2   https://whatsgabycooking.com/raspberry-brownies/  233 kcal   
3  https://whatsgabycooking.com/pineapple-sheet-c...  611 kcal   
4   https://whatsgabycooking.com/magic-bar-brownies/  166 kcal   

  carbohydrateContent proteinContent fatContent saturatedFatContent  \
0                67 g            8 g       49 g                31 g   
1                45 g            4 g       19 g                13 g   
2                47 g            3 g        5 g                 2 g   
3                76 g            7 g       32 g                19 g   
4                23 g            3 g        7 g                 4 g   

  transFatContent cholesterolContent sodiumContent fiberContent sugarContent  \
0             1 g             145 mg        500 mg          3 g         31 g   
1           0.5 g              94 mg         42 mg          1 g         37 g   
2         0.002 g              28 mg        152 mg          1 g         36 g   
3             1 g             104 mg        131 mg          2 g         65 g   
4             NaN              29 mg         62 mg          2 g         20 g   

  unsaturatedFatContent servingSize  
0                  14 g   1 serving  
1                   5 g   1 serving  
2                 1.3 g   1 serving  
3                  10 g   1 serving  
4                 2.3 g   1 serving

In [18]:
# make note of dietary restrictions 
indr[indr['dietary_restrictions'].notna()]
# only present for 1250 recipes 

ingredients  \
4259  [1 ball Best Pizza Dough (or Thin Crust Dough)...   
4260  [¾ cup unsalted cashews, 1 medium yellow onion...   
4263  [1 ½ ounces (3 tablespoons) tequila blanco or ...   
4264  [1 pound ripe strawberries, 3 tablespoons suga...   
4267  [1 ¾ cups [245 g] all-purpose flour, ½ cup [10...   
...                                                 ...   
7494  [1 ¼ cup all-purpose flour, 3/4 cup light brow...   
7499  [1 cup dried chickpeas (not cooked or canned),...   
7502  [⅓ cup hummus, 8 English cucumber slices (or s...   
7505  [2 cups Old Fashioned rolled oats (don’t subst...   
7512  [2 tablespoons cornstarch , 1 ½ cups whole mil...   

                                              nutrients dietary_restrictions  
4259  {'servingSize': '1 slice', 'calories': '121 ca...    [Vegetarian Diet]  
4260  {'calories': '380 calories', 'sugarContent': '...         [Vegan Diet]  
4263  {'calories': '166 calories', 'sugarContent': '...         [Vegan Diet]  
4264  {'calories': '310 calories', 'sugarContent': '...    [Vegetarian Diet]  
4267  {'calories': '267 calories', 'sugarContent': '...    [Vegetarian Diet]  
...                                                 ...                  ...  
7494  {'calories': '207 calories', 'sugarContent': '...    [Vegetarian Diet]  
7499  {'servingSize': '4 falafel', 'calories': '258 ...         [Vegan Diet]  
7502  {'calories': '552 calories', 'sugarContent': '...         [Vegan Diet]  
7505  {'calories': '293 calories', 'sugarContent': '...         [Vegan Diet]  
7512  {'calories': '312 calories', 'sugarContent': '...    [Vegetarian Diet]  

[1250 rows x 3 columns]

In [ ]:
# recipies can now be slected based on calories, macronutrients, ingredients, and dietary restrictions

# using your pantry 

# nl text input for ingredients through pipeline to match df 
# if all ingreidients are in your pantry you can make 
# if most ~80%+ ingredients in your pantry tehn also recommend with a note 

In [268]:
import speech_recognition as sr
from pydub import AudioSegment

from pydub import AudioSegment
import os

# Get the path of ffmpeg installed in Anaconda
ffmpeg_path = "/Users/bryce/anaconda3/bin/ffmpeg" 
# Set FFmpeg path
AudioSegment.converter = ffmpeg_path

def convert_m4a_to_wav(m4a_path, wav_path):
    """Convert .m4a file to .wav format using pydub."""
    audio = AudioSegment.from_file(m4a_path, format="m4a")
    audio.export(wav_path, format="wav")

def transcribe_audio(audio_path):
    """Convert speech to text from a .wav file."""
    recognizer = sr.Recognizer()
    
    with sr.AudioFile(audio_path) as source:
        audio = recognizer.record(source)  # Read the file

    try:
        text = recognizer.recognize_google(audio)
        print("📝 Transcription:", text)
        return text
    except sr.UnknownValueError:
        print("❌ Could not understand the audio")
    except sr.RequestError:
        print("❌ Could not request results (Check Internet)")

# Convert and transcribe
m4a_file = 'audio recording/mypantry.m4a'  # Replace with your file path
wav_file = "converted.wav"

convert_m4a_to_wav(m4a_file, wav_file)
my_pantry = transcribe_audio(wav_file)

📝 Transcription: soy sauce apple cider vinegar balsamic vinegar Panko bread crumbs sesame oil canola oil clover honey Worcestershire sauce salt cornstarch baking powder peanut butter macaroni noodles penne pasta spaghetti thin spaghetti Ritz crackers popcorn seasoning salt Old Bay Seasoning tomato paste diced tomatoes black beans vanilla baking soda pepper ground nutmeg Italian seasoning onion powder ground cinnamon garlic powder oregano sea salt pepper ground ginger Cayenne paprika chili powder steak seasoning red pepper Rosemary basil parsley vegetable oil white vinegar butter garlic strawberry jelly Dijon mustard Ginger paste Caesar dressing mayonnaise barbecue sauce mustard ranch ketchup maple syrup thousand island dressing honey mustard chili sauce beef broth chicken broth heavy whipping cream milk lemon juice white wine yogurt ricotta cheese strawberries blackberries eggs carrots ice cream frozen green beans shrimp frozen shrimp fruit frozen fruit frozen strawberries bacon


In [269]:
m4a_file = 'audio recording/mypantry2.m4a'  # Replace with your file path
wav_file = "converted.wav"
convert_m4a_to_wav(m4a_file, wav_file)
my_pantry2 = transcribe_audio(wav_file)

📝 Transcription: sugar brown sugar powdered sugar all purpose flour granulated sugar chocolate chips white chocolate chips cake flour brownie mix onions potatoes


In [270]:
my_pantry = my_pantry +" rice water hot water cold water "+my_pantry2

In [221]:
my_pantry

'soy sauce apple cider vinegar balsamic vinegar Panko bread crumbs sesame oil canola oil clover honey Worcestershire sauce salt cornstarch baking powder peanut butter macaroni noodles penne pasta spaghetti thin spaghetti Ritz crackers popcorn seasoning salt Old Bay Seasoning tomato paste diced tomatoes black beans vanilla baking soda pepper ground nutmeg Italian seasoning onion powder ground cinnamon garlic powder oregano sea salt pepper ground ginger Cayenne paprika chili powder steak seasoning red pepper Rosemary basil parsley vegetable oil white vinegar butter garlic strawberry jelly Dijon mustard Ginger paste Caesar dressing mayonnaise barbecue sauce mustard ranch ketchup maple syrup thousand island dressing honey mustard chili sauce beef broth chicken broth heavy whipping cream milk lemon juice white wine yogurt ricotta cheese strawberries blackberries eggs carrots ice cream frozen green beans shrimp frozen shrimp fruit frozen fruit frozen strawberries bacon rice sugar brown sugar

In [271]:
#extract ings 
my_pantry_list = []
for item in list(poss_ing_update):
    if item in my_pantry:
        my_pantry_list.append(item)

In [272]:
ingredient_df_c["recipe_sum"] = ingredient_df_c.drop(columns=["recipe_id"]).sum(axis=1)

# my_pantry = {"garlic", "olive oil", "salt"}  # Replace with your pantry items

# Select only columns that match pantry ingredients
available_cols = [col for col in ingredient_df_c.columns if col in my_pantry_list]
#get proportion of recipe that uses ingredients I have

# what recipes use ingredients that i have
ingredient_df_c["pantry_sum"] = ingredient_df_c[available_cols].sum(axis=1)
mp_df= ingredient_df_c[ingredient_df_c["pantry_sum"]>0]
mp_df["on_hand_proportion"] = mp_df["pantry_sum"] / mp_df["recipe_sum"]


# print(available_cols)
# available_cols.append("recipe_id")
# available_cols.append("ingredient_sum")
# available_cols.append("pantry_sum")
# # Keep recipes where all used ingredients are in pantry (i.e., no extra ingredients)
# mp_df = ingredient_df[available_cols]


mp_df.sort_values("on_hand_proportion", ascending = False) 

/var/folders/yr/ck3hvtw16ks5djc79x7fgf6r0000gn/T/ipykernel_38727/3463127546.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  mp_df["on_hand_proportion"] = mp_df["pantry_sum"] / mp_df["recipe_sum"]


recipe_id  \
4193   https://www.wellplated.com/sweet-potato-souffle/   
4269   https://www.acouplecooks.com/vegetarian-fajitas/   
3854             https://www.wellplated.com/corn-salsa/   
3638  https://www.wellplated.com/cranberry-turkey-me...   
4836  https://www.acouplecooks.com/chicken-meatballs...   
...                                                 ...   
1318  https://whatsgabycooking.com/caramelized-mushr...   
2485                                                NaN   
1159  https://whatsgabycooking.com/100-best-snacks-f...   
2363                                                NaN   
2187                                                NaN   

      mini dark chocolate chips  gruyere cheese  japanese cucumbers  \
4193                          0               0                   0   
4269                          0               0                   0   
3854                          0               0                   0   
3638                          0               0                   0   
4836                          0               0                   0   
...                         ...             ...                 ...   
1318                          0               0                   0   
2485                          0               0                   0   
1159                          0               0                   0   
2363                          0               0                   0   
2187                          0               0                   0   

      simply nature organic classic hummus  full fat sour cream  croissants  \
4193                                     0                    0           0   
4269                                     0                    0           0   
3854                                     0                    0           0   
3638                                     0                    0           0   
4836                                     0                    0           0   
...                                    ...                  ...         ...   
1318                                     0                    0           0   
2485                                     0                    0           0   
1159                                     0                    0           0   
2363                                     0                    0           0   
2187                                     0                    0           0   

      heirloom plum tomatoes  fresh chives from the aerogarden  \
4193                       0                                 0   
4269                       0                                 0   
3854                       0                                 0   
3638                       0                                 0   
4836                       0                                 0   
...                      ...                               ...   
1318                       0                                 0   
2485                       0                                 0   
1159                       0                                 0   
2363                       0                                 0   
2187                       0                                 0   

      -cheese tortellini  canned mexicorn  raw pepitas  aged rum  \
4193                   0                0            0         0   
4269                   0                0            0         0   
3854                   0                0            0         0   
3638                   0                0            0         0   
4836                   0                0            0         0   
...                  ...              ...          ...       ...   
1318                   0                0            0         0   
2485                   0                0            0         0   
1159                   0                0            0         0   
2363                   0                0            0        